# Une méthode pour filtrer les données

### Problématique

Les zones d'autorisation sont représentées par des points placés à certains endroits. Ces points sont plus ou moins espacés et semblent remplir l"espace pour former des zones. Les coordonnées des stations météo et des parcs éoliens existants sont également représentées par des points.

Pour filtrer et comparer ces données, il n"est pas possible de simplement soustraire les coordonnées, car la probabilité qu'une station météo se trouve exactement au même endroit qu'un point d'une zone est presque nulle.

Pour résoudre cette problématique, nous avons d'abord essayé la méthode du `ray casting`, qui consiste à projeter une droite dans toutes les directions autour d'un point jusqu'à rencontrer un autre point. Cette méthode est efficace pour les points situés sur le périmètre d'un polygone, mais moins adaptée lorsque les points remplissent l'aire de celui-ci. Nous avons également tenté d'utiliser la méthode `k-means` pour réduire la taille des zones à tester, mais les résultats n'ont pas été concluants.

Nous avons donc décidé de repartir de zéro en reformulant la question : **À quelle distance d'une zone se trouve une station météo ?**

Cette approche introduit immédiatement la notion de rayon autour d'un point et élimine la nécessité de superposer les points.

Après quelques recherches, nous avons découvert la formule de `Haversine`. Il s'agit d'une formule utilisée pour calculer la distance entre deux points sur une sphère à partir de leurs coordonnées de longitude et de latitude. En termes plus simples, elle permet de calculer la distance la plus courte entre deux points à la surface d'un objet sphérique, comme la Terre. Il suffisait ensuite de préciser une distance maximale autorisée, et le problème était résolu.

## 1. Les bases

Executer ce code

In [2]:
import random

import pandas as pd
import numpy as np
import plotly.express as px

In [3]:
R = 6371  # Earth Radius in kilometers
MAX_DIST = 30 # kilometers

In [7]:
def haversine(lat1: float, lon1: float, lat2: float, lon2: float) -> float:
    lat1, lon1, lat2, lon2 = map(np.radians, [lat1, lon1, lat2, lon2])

    dlat = lat2 - lat1
    dlon = lon2 - lon1

    a = np.sin(dlat/2)**2 + np.cos(lat1) * np.cos(lat2) * np.sin(dlon/2)**2
    c = 2 * np.arcsin(np.sqrt(a))

    return c * R


def check_authorization(df_zones: pd.DataFrame, df_positions: pd.DataFrame):
    authorized_positions = []

    for _, pos in df_positions.iterrows():
        pos_lat, pos_lon = pos["LAT"], pos["LON"]
        is_authorized = False
        
        for _, zone in df_zones.iterrows():
            zone_lat, zone_lon, zone_radius = zone["LAT"], zone["LON"], zone["Radius"]
            distance = haversine(pos_lat, pos_lon, zone_lat, zone_lon)
            
            if distance <= zone_radius:
                is_authorized = True
                break

        authorized_positions.append(is_authorized)

    df_positions["is_authorized"] = authorized_positions
    return df_positions

## 2. Un peu de recherche

Il n'est pas nécessaire d'executer ce code

In [15]:
df_zones = pd.read_csv("s3://jedha-final-project-jrat/zones.csv")
df_zones.head()

Y    X   Latitude  Longitude             Color
0  79  571  50.198832   3.355932  rgb(206,136,255)
1  80  571  50.188113   3.355932  rgb(206,136,255)
2  80  579  50.188113   3.480975  rgb(208,142,255)
3  81  572  50.177394   3.371562  rgb(206,136,255)
4  83  577  50.155957   3.449714  rgb(208,142,255)

In [8]:
df_positions = pd.DataFrame({
    "Latitude": [random.uniform(43, 50) for _ in range(200)],
    "Longitude": [random.uniform(-1, 10) for _ in range(200)]
})
df_positions.head()  # remplacer par les vraies positions des stations meteo ou parcs eoliens

Latitude  Longitude
0  48.132028   6.578735
1  44.308478   1.334661
2  49.255882   4.396361
3  46.773663   9.434161
4  46.117363   9.247404

In [19]:
df_zones["Radius"] = MAX_DIST
df_positions_filtered = check_authorization(df_zones, df_positions)

df_positions_filtered.head()


C:\Users\giand\AppData\Local\Temp\ipykernel_1160\4143877806.py:30: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_positions["is_authorized"] = authorized_positions


NUM_POSTE       NOM_USUEL        LAT       LON  ALTI      AAAAMM  Year  \
0       1014002          ARBENT  46.278167  5.669000   534  2004-03-01  2004   
226     1033002      BELLEGARDE  46.086500  5.814167   350  1994-04-01  1994   
570     1034004          BELLEY  45.769333  5.688000   330  2001-10-01  2001   
825     1071001           CESSY  46.310333  6.080333   507  2002-05-01  2002   
1073    1072001  CEYZERIAT_SAPC  46.204333  5.287667   260  1994-08-01  1994   

      Month  precip_cumul_mensu  temp_mean_mensu  ...  \
0         3                23.8             12.7  ...   
226       4               144.4             12.7  ...   
570      10                98.4             20.8  ...   
825       5               145.8             18.6  ...   
1073      8                36.0             26.9  ...   

      vent_speed_inst_max_mensu  vent_dir_inst  vent_nbjour_inst_speedsup10ms  \
0                          50.4          300.0                            6.0   
226                        57.6          220.0                           12.0   
570                        90.0          200.0                            5.0   
825                        61.2          340.0                            7.0   
1073                       43.2          220.0                            4.0   

      vent_speed_10mn_max_mensu  vent_dir_10mn  vent_nbjour_10mn_speedsup10ms  \
0                          25.2          360.0                            0.0   
226                        28.8           50.0                            0.0   
570                        50.4          200.0                            1.0   
825                        36.0          340.0                            1.0   
1073                       21.6          190.0                            0.0   

      departement_num  departement_name                region  is_authorized  
0                   1               Ain  AUVERGNE RHONE ALPES           True  
226                 1               Ain  AUVERGNE RHONE ALPES           True  
570                 1               Ain  AUVERGNE RHONE ALPES          False  
825                 1               Ain  AUVERGNE RHONE ALPES           True  
1073                1               Ain  AUVERGNE RHONE ALPES           True  

[5 rows x 27 columns]

In [10]:
df_positions["is_authorized"] = df_positions["is_authorized"].astype(str)

# zones
fig = px.scatter_mapbox(
    df_zones, 
    lat="Latitude", 
    lon="Longitude",
    zoom=5,
    height=800
)

fig.update_traces(marker=dict(size=MAX_DIST, color="gray"))

# stations or parks
fig.add_scattermapbox(
    lat=df_positions["LAT"], 
    lon=df_positions["LON"], 
    mode="markers",
    marker=dict(size=10),
    marker_color=df_positions["is_authorized"].map({"True": "green", "False": "red"})
)

fig.update_layout(mapbox_style="open-street-map")
fig.show()


![](https://raw.githubusercontent.com/tristanGIANDO/jedha_final_project/develop/jedha_final_project/src/filter_haversine.png)

---

## 3. Filtering Meteo stations

Voilà le code à executer en prod

In [4]:
df_positions = pd.read_csv("https://jedha-final-project-jrat.s3.amazonaws.com/datameteo_france_1950-2022_clean_03.csv")
df_zones = pd.read_csv("s3://jedha-final-project-jrat/zones_03.csv")

In [12]:
df_positions = df_positions.drop_duplicates(subset=["LAT", "LON"])
df_positions.head()

NUM_POSTE       NOM_USUEL        LAT       LON  ALTI      AAAAMM  Year  \
0       1014002          ARBENT  46.278167  5.669000   534  2004-03-01  2004   
226     1033002      BELLEGARDE  46.086500  5.814167   350  1994-04-01  1994   
570     1034004          BELLEY  45.769333  5.688000   330  2001-10-01  2001   
825     1071001           CESSY  46.310333  6.080333   507  2002-05-01  2002   
1073    1072001  CEYZERIAT_SAPC  46.204333  5.287667   260  1994-08-01  1994   

      Month  precip_cumul_mensu  temp_mean_mensu  ...  \
0         3                23.8             12.7  ...   
226       4               144.4             12.7  ...   
570      10                98.4             20.8  ...   
825       5               145.8             18.6  ...   
1073      8                36.0             26.9  ...   

      vent_speed_inst_moy_mensu  vent_speed_inst_max_mensu  vent_dir_inst  \
0                           7.6                       50.4          300.0   
226                         5.8                       57.6          220.0   
570                         5.8                       90.0          200.0   
825                         6.8                       61.2          340.0   
1073                        5.4                       43.2          220.0   

      vent_nbjour_inst_speedsup10ms  vent_speed_10mn_max_mensu  vent_dir_10mn  \
0                               6.0                       25.2          360.0   
226                            12.0                       28.8           50.0   
570                             5.0                       50.4          200.0   
825                             7.0                       36.0          340.0   
1073                            4.0                       21.6          190.0   

      vent_nbjour_10mn_speedsup10ms  departement_num  departement_name  \
0                               0.0                1               Ain   
226                             0.0                1               Ain   
570                             1.0                1               Ain   
825                             1.0                1               Ain   
1073                            0.0                1               Ain   

                    region  
0     AUVERGNE RHONE ALPES  
226   AUVERGNE RHONE ALPES  
570   AUVERGNE RHONE ALPES  
825   AUVERGNE RHONE ALPES  
1073  AUVERGNE RHONE ALPES  

[5 rows x 26 columns]

Première méthode mais c'est très long

In [8]:
df_zones["Radius"] = MAX_DIST
df_positions_filtered = check_authorization(df_zones, df_positions)

df_positions_filtered.head()

KeyboardInterrupt: 

Méthode optimisée

In [5]:
import numpy as np
import pandas as pd
from sklearn.neighbors import BallTree

# Constante pour le rayon de la Terre en kilomètres
R = 6371.0

def haversine_vectorized(lat1, lon1, lat2, lon2):
    # Conversion en radians
    lat1, lon1, lat2, lon2 = np.radians([lat1, lon1, lat2, lon2])

    dlat = lat2 - lat1
    dlon = lon2 - lon1

    a = np.sin(dlat / 2.0) ** 2 + np.cos(lat1) * np.cos(lat2) * np.sin(dlon / 2.0) ** 2
    c = 2 * np.arcsin(np.sqrt(a))

    return c * R

def check_authorization_optimized(df_zones: pd.DataFrame, df_positions: pd.DataFrame):
    # Convertir les latitudes et longitudes des zones en radians
    zones_radians = np.radians(df_zones[["LAT", "LON"]])
    # Création du BallTree pour les zones
    tree = BallTree(zones_radians, metric='haversine')
    
    # Convertir les positions en radians
    positions_radians = np.radians(df_positions[["LAT", "LON"]])
    
    # Chercher toutes les zones dans un rayon maximal
    max_radius = df_zones["Radius"].max() / R  # On normalise le rayon par le rayon de la Terre
    indices = tree.query_radius(positions_radians, r=max_radius)
    
    authorized_positions = []

    # Parcourir chaque position et filtrer les zones en fonction de leur rayon spécifique
    for i, nearby_zones in enumerate(indices):
        pos_lat = df_positions.iloc[i]["LAT"]
        pos_lon = df_positions.iloc[i]["LON"]
        is_authorized = False

        for zone_index in nearby_zones:
            zone_lat = df_zones.iloc[zone_index]["LAT"]
            zone_lon = df_zones.iloc[zone_index]["LON"]
            zone_radius = df_zones.iloc[zone_index]["Radius"]
            
            # Calculer la distance réelle
            distance = haversine_vectorized(pos_lat, pos_lon, zone_lat, zone_lon)
            
            if distance <= zone_radius:
                is_authorized = True
                break
        
        authorized_positions.append(is_authorized)
    
    df_positions["is_authorized"] = authorized_positions
    return df_positions



In [6]:
df_zones["Radius"] = 10
df_positions_filtered = check_authorization_optimized(df_zones, df_positions)

df_positions_filtered.head()

NUM_POSTE NOM_USUEL        LAT    LON  ALTI      AAAAMM  Year  Month  \
0    1014002    ARBENT  46.278167  5.669   534  2004-03-01  2004      3   
1    1014002    ARBENT  46.278167  5.669   534  2004-04-01  2004      4   
2    1014002    ARBENT  46.278167  5.669   534  2004-05-01  2004      5   
3    1014002    ARBENT  46.278167  5.669   534  2004-06-01  2004      6   
4    1014002    ARBENT  46.278167  5.669   534  2004-07-01  2004      7   

   precip_cumul_mensu  temp_mean_mensu  ...  vent_speed_inst_max_mensu  \
0                23.8             12.7  ...                       50.4   
1                44.8             14.5  ...                       54.0   
2                95.0             18.8  ...                       50.4   
3                56.3             23.6  ...                       64.8   
4                61.3             25.3  ...                       64.8   

   vent_dir_inst  vent_nbjour_inst_speedsup10ms  vent_speed_10mn_max_mensu  \
0          300.0                            6.0                       25.2   
1          220.0                           17.0                       32.4   
2          340.0                           13.0                       32.4   
3          160.0                           15.0                       28.8   
4          210.0                           14.0                       36.0   

   vent_dir_10mn  vent_nbjour_10mn_speedsup10ms  departement_num  \
0          360.0                            0.0                1   
1          210.0                            0.0                1   
2          330.0                            0.0                1   
3          170.0                            0.0                1   
4          150.0                            1.0                1   

   departement_name                region  is_authorized  
0               Ain  AUVERGNE RHONE ALPES           True  
1               Ain  AUVERGNE RHONE ALPES           True  
2               Ain  AUVERGNE RHONE ALPES           True  
3               Ain  AUVERGNE RHONE ALPES           True  
4               Ain  AUVERGNE RHONE ALPES           True  

[5 rows x 27 columns]

In [7]:
df_to_export = df_positions_filtered
df_positions_filtered = df_positions_filtered.drop_duplicates(subset=["LAT", "LON"])
df_positions_filtered["is_authorized"] = df_positions_filtered["is_authorized"].astype(str)

# zones
fig = px.scatter_mapbox(
    df_zones, 
    lat="LAT", 
    lon="LON",
    zoom=5,
    height=800
)

fig.update_traces(marker=dict(size=10, color="gray"))

# stations or parks
fig.add_scattermapbox(
    lat=df_positions_filtered["LAT"], 
    lon=df_positions_filtered["LON"], 
    mode="markers",
    marker=dict(size=10),
    marker_color=df_positions_filtered["is_authorized"].map({"True": "green", "False": "red"})
)

fig.update_layout(mapbox_style="open-street-map")
fig.show()

C:\Users\giand\AppData\Local\Temp\ipykernel_11572\2671534303.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_positions_filtered["is_authorized"] = df_positions_filtered["is_authorized"].astype(str)


In [9]:
df_to_export.shape

(340387, 27)

In [10]:
df_to_export.to_csv("datameteo_france_1950-2022_clean_04.csv", index=False)